In [ ]:
%matplotlib inline


# Parametric scalable MDO problem - MDF
We define a scalable problem based on two strongly coupled disciplines
and a weakly one, with the following properties:

- 3 shared design parameters,
- 2 local design parameters for the first strongly coupled discipline,
- 2 coupling variables for the first strongly coupled discipline,
- 4 local design parameters for the second strongly coupled discipline,
- 3 coupling variables for the second strongly coupled discipline.

We would like to solve this MDO problem by means of an MDF formulation.


In [ ]:
from __future__ import division, unicode_literals

from gemseo.api import configure_logger, generate_n2_plot
from gemseo.problems.scalable.parametric.problem import TMScalableProblem
from gemseo.uncertainty.umdo.umdo_scenario import UMDOScenario

configure_logger()

## Instantiation of the scalable problem



In [ ]:
n_shared = 3
n_local = [2, 4]
n_coupling = [2, 3]
problem = TMScalableProblem(n_shared, n_local, n_coupling, noised_coupling=True)

## Display the coupling structure



In [ ]:
generate_n2_plot(problem.disciplines, save=False, show=True)

## Solve the U-MDO using an MDF formulation



In [ ]:
sampling_options = {"algo": "OT_MONTE_CARLO", "n_samples": 100}
scenario = UMDOScenario(
    problem.disciplines,
    "UMDF",
    "obj",
    problem.design_space,
    sampling_options=sampling_options,
)

We set the robustness measures for the objective and the constraints.



In [ ]:
scenario.set_robustness_measure("obj", "mean")
scenario.set_robustness_measure("cstr_0", "mean_std", std_factor=3.0)
scenario.set_robustness_measure("cstr_1", "mean_std", std_factor=3.0)
scenario.add_constraint("cstr_0", "ineq", "p_cstr_0", value=0.0)
scenario.add_constraint("cstr_1", "ineq", "p_cstr_1", value=0.0)

Display XDSM



In [ ]:
scenario.xdsmize(latex_output=True)

Execute



In [ ]:
scenario.execute({"algo": "NLOPT_COBYLA", "max_iter": 100, "xtol_abs": 1e-3})

## Post-process the results



In [ ]:
scenario.post_process("OptHistoryView", save=False, show=True)